In [1]:
import pandas as pd
import os
from demoparser2 import DemoParser


In [2]:
demo_files = [f for f in os.listdir("../demos/") if f.endswith(".dem")]
print(demo_files.__len__())
all_rounds_data = []

76


In [11]:
for demo_file in demo_files:
    parser = DemoParser(f"../demos/{demo_file}")
    
    wanted_ticks = parser.parse_event("round_freeze_end")["tick"].tolist()
    wanted_props = [
        "kills_total", "deaths_total", "balance", "current_equip_value",
        "round_start_equip_value", "total_rounds_played", "team_num",
        "inventory", "has_helmet", "has_defuser", "armor_value", "team_clan_name"
    ]
    player_data = parser.parse_ticks(wanted_props, ticks=wanted_ticks)
    
    round_end_data = parser.parse_event("round_end")[['tick', 'winner']]
    round_end_data['total_rounds_played'] = range(len(round_end_data))

    grouped_player_data = player_data.groupby('total_rounds_played')
    grouped_round_end_data = round_end_data.groupby('total_rounds_played').last()

    for name, group in grouped_player_data:
        round_winner = grouped_round_end_data.loc[name, 'winner'] if name in grouped_round_end_data.index else None
        
        pivot_columns = {
            'team_clan_name': 'player_{}_team_name',
            'name': 'player_{}_name',
            'team_num': 'player_{}_team_num',
            'kills_total': 'player_{}_kills_total',
            'deaths_total': 'player_{}_deaths_total',
            'inventory': 'player_{}_inventory',
            'has_defuser': 'player_{}_has_defuser',
            'has_helmet': 'player_{}_has_helmet',
            'armor_value': 'player_{}_armor_value',
            'current_equip_value': 'player_{}_current_equip_value',
            'balance': 'player_{}_balance'
        }

        round_df = pd.DataFrame()
        player_idx = 1

        for idx, row in group.iterrows():
            if player_idx > 10:
                break
            for key, val in pivot_columns.items():
                round_df[val.format(player_idx)] = [row[key]]
            player_idx += 1

        if round_winner:
            round_df['round_winner'] = round_winner

        all_rounds_data.append(round_df)


C:\Users\Cosmin\AppData\Local\Temp\ipykernel_28504\3875549348.py:42: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  round_df[val.format(player_idx)] = [row[key]]
C:\Users\Cosmin\AppData\Local\Temp\ipykernel_28504\3875549348.py:42: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  round_df[val.format(player_idx)] = [row[key]]
C:\Users\Cosmin\AppData\Local\Temp\ipykernel_28504\3875549348.py:42: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performanc

In [12]:
final_df = pd.concat(all_rounds_data, ignore_index=True)
final_df.to_csv('complete_rounds_data.csv', index=False)